In [1]:
import numpy as np
import scipy as sp
from scipy import sparse as sps
import scipy.sparse.linalg as la
import pylab as pl
%matplotlib

Using matplotlib backend: Qt5Agg


In [2]:
# construct operator in single site
def singlesiteoperators(Op, i, L, Iden):
    opls    = [Iden]*L  # create 2x2 identity matrix L of them in a list
    opls[i] = Op        # Put the opeartor which one needs to kron with identity
    
    f_op= opls[0]
    # now lets do the kron
    for i in range(L-1):
        f_op = sps.kron(f_op, opls[i+1], format='csr')
    
    return f_op

In [27]:
# different matrices
Id = sps.csr_matrix(np.eye(2))
Sx = sps.csr_matrix([[0., 1.], [1., 0.]])
Sz = sps.csr_matrix([[1., 0.], [0., -1.]])

# system size
Ll=4

SxFull = [singlesiteoperators(Sx, L, Ll, Id) for L in range(Ll)]

SzFull = [singlesiteoperators(Sz, L, Ll, Id) for L in range(Ll)]

In [28]:
def ising_hamiltonian(L, Sxlist, Szlist, g):
    """
    L- system size
    Sxlist - all sx operators
    Sylist - all sy operators
    g - coupling strength (here J is taken to be 1)
    """
    ham = sps.csr_matrix((2**L, 2**L))
    for k in range(L):
        knext = np.mod(k+1,L)
        
        ham += -Sxlist[k]*Sxlist[knext] - g*Szlist[k]
        
    return ham

In [29]:
# sparse hamiltonian
ham = ising_hamiltonian(Ll, SxFull, SzFull, 1.0)

print(repr(ham))

print(ham.toarray())

<16x16 sparse matrix of type '<class 'numpy.float64'>'
	with 74 stored elements in Compressed Sparse Row format>
[[-4.  0.  0. -1.  0.  0. -1.  0.  0. -1.  0.  0. -1.  0.  0.  0.]
 [ 0. -2. -1.  0.  0.  0.  0. -1. -1.  0.  0.  0.  0. -1.  0.  0.]
 [ 0. -1. -2.  0. -1.  0.  0.  0.  0.  0.  0. -1.  0.  0. -1.  0.]
 [-1.  0.  0.  0.  0. -1.  0.  0.  0.  0. -1.  0.  0.  0.  0. -1.]
 [ 0.  0. -1.  0. -2.  0.  0. -1. -1.  0.  0.  0.  0. -1.  0.  0.]
 [ 0.  0.  0. -1.  0.  0. -1.  0.  0. -1.  0.  0. -1.  0.  0.  0.]
 [-1.  0.  0.  0.  0. -1.  0.  0.  0.  0. -1.  0.  0.  0.  0. -1.]
 [ 0. -1.  0.  0. -1.  0.  0.  2.  0.  0.  0. -1.  0.  0. -1.  0.]
 [ 0. -1.  0.  0. -1.  0.  0.  0. -2.  0.  0. -1.  0.  0. -1.  0.]
 [-1.  0.  0.  0.  0. -1.  0.  0.  0.  0. -1.  0.  0.  0.  0. -1.]
 [ 0.  0.  0. -1.  0.  0. -1.  0.  0. -1.  0.  0. -1.  0.  0.  0.]
 [ 0.  0. -1.  0.  0.  0.  0. -1. -1.  0.  0.  2.  0. -1.  0.  0.]
 [-1.  0.  0.  0.  0. -1.  0.  0.  0.  0. -1.  0.  0.  0.  0. -1.]
 [ 0. -1.  0.  0

In [30]:
# diagonalize the hamiltonian
evals, evecs = la.eigsh(ham, which='SA')

print(evals)

[-5.22625186 -4.82842712 -2.1647844  -2.         -2.         -0.82842712]


In [31]:
## check with usual full diagonalization
evals, evecs = np.linalg.eigh(ham.toarray())

print(evals)

[-5.22625186e+00 -4.82842712e+00 -2.16478440e+00 -2.00000000e+00
 -2.00000000e+00 -8.28427125e-01 -9.52242404e-17 -4.61542421e-17
  2.15619877e-16  4.45994233e-16  8.28427125e-01  2.00000000e+00
  2.00000000e+00  2.16478440e+00  4.82842712e+00  5.22625186e+00]


In [41]:
## plot the ground state and first excited state as function of g
glist = np.linspace(0, 2, 11)

e0=[]
e1=[]

for g in glist:
    ham = ising_hamiltonian(Ll, SxFull, SzFull, g)
    
    evals, evecs = la.eigsh(ham, which='SA')
    
    e0.append(evals[0])
    e1.append(evals[1])

In [54]:
# plot them
pl.figure(0)
pl.plot(glist, e0, '--', lw=2)
pl.plot(glist, e1)

In [53]:
# plot the gap
pl.figure(1)
pl.plot(glist,np.array(e1)-np.array(e0), 'o', mfc='none')
pl.axvline(1,color='k', lw=0.5)
pl.axhline(0,color='k', lw=0.5)

# Gap scaling

In [61]:
# now do it for different values of L
Ll=[4,6,8,]

## plot the ground state and first excited state as function of g
glist = np.linspace(0, 2, 11)

# loop for system sizes
for L in Ll:

    ## also create all the operators
    SxFull = [singlesiteoperators(Sx, k, L, Id) for k in range(L)]
    SzFull = [singlesiteoperators(Sz, k, L, Id) for k in range(L)]
    
    ## save the gap here
    gap_delta=[]
    for g in glist:
        # create hamiltonian
        ham = ising_hamiltonian(L, SxFull, SzFull, g)
        # diagonalize
        evals, evecs = la.eigsh(ham, which='SA')

        gap_delta.append(evals[1]-evals[0])
        
    # plot it
    pl.plot(glist, gap_delta, 'o', label=r'$L='+str(L)+'$',mfc='none')
    
pl.axvline(1,color='k', lw=0.5)
pl.axhline(0,color='k', lw=0.5)
pl.legend(loc='best')

# correlation function

In [94]:
# calculate the correlation function as a function of site
# system size
Ll=6

SxFull = [singlesiteoperators(Sx, L, Ll, Id) for L in range(Ll)]
SzFull = [singlesiteoperators(Sz, L, Ll, Id) for L in range(Ll)]

#for i in range(L-1):
sxsx = SxFull[0]*SxFull[1]
szsz = SzFull[0]*SzFull[1]

glist = np.linspace(0, 2, 21)
#
corr=[]
for g in glist:
    # create hamiltonian
    ham = ising_hamiltonian(Ll, SxFull, SzFull, g)
    # diagonalize
    evals, evecs = la.eigsh(ham, which='SA')

    corr.append( ( np.dot(evecs[:,0].T, sxsx@evecs[:,0]), np.dot(evecs[:,0].T, szsz@evecs[:,0]) ))
    

pl.plot(glist, np.array(corr)[:,0],label='x-x')
pl.plot(glist, np.array(corr)[:,1],label='z-z')

pl.legend(loc='best')

In [157]:
# correlation deep in the phase
# calculate the correlation function as a function of site
# system size
Ll=6

SxFull = [singlesiteoperators(Sx, L, Ll, Id) for L in range(Ll)]
SzFull = [singlesiteoperators(Sz, L, Ll, Id) for L in range(Ll)]
sxsx=[]
for i in range(Ll//2+1):
    sxsx.append( SxFull[0]*SxFull[i] )

corr=[]
g=10.0
# create hamiltonian
ham = ising_hamiltonian(Ll, SxFull, SzFull, g)
# diagonalize
evals, evecs = la.eigsh(ham, which='SA')

corr=[ np.dot(evecs[:,0].T, sxsx[i]@evecs[:,0]) for i in range(Ll//2+1)]
# print(corr)    

pl.plot(1+np.arange(Ll//2+1), np.array(corr), '--+')

pl.semilogy()
# pl.semilogx()

[]